In [1]:
import numpy as np
import netket as nk
from scripts import functions as f
from scripts import new_dynamics

/home/keisuke/Documents/Research/sshfs/DimerMaster/scripts/functions.py:65: NumbaDeprecationWarning: The 'numba.jitclass' decorator has moved to 'numba.experimental.jitclass' to better reflect the experimental nature of the functionality. Please update your imports to accommodate this change and see https://numba.pydata.org/numba-doc/latest/reference/deprecation.html#change-of-jitclass-location for the time frame.
  @jitclass(spec)


In [2]:
import scripts.utils as utils

In [3]:
from importlib import reload

In [4]:
import multiprocessing as mp

In [34]:
import mkl
import time
mkl.set_num_threads(12)

1

In [6]:
mkl.get_max_threads()

1

In [7]:
from conf import *
from numba import njit, jit

In [8]:
h = 1.0
V = 1.1

length = [12, 12]
name = 'h={}V={}l={}'.format(h, V, length)
kernel = 1
n_chains = 1
n_discards = 1
n_samples = 2000
alpha = 1
g = nk.graph.Graph(nodes = [i for i in range(length[0] * length[1] * 2)])
hi = nk.hilbert.Spin(s=0.5, graph=g)

op = f.dimer_hamiltonian(V = V, h = h,length = np.array(length))
op_transition = f.dimer_flip1(length = np.array(length))
hex_ = nk.machine.new_hex(np.array(length))


ma = nk.machine.RbmDimer(hi, hex_, alpha = alpha, symmetry = True
                    ,use_hidden_bias = False, use_visible_bias = False, dtype=float, reverse=True, half=True)

# ma.load('save/ma/'+name)
ma.init_random_parameters()

1


In [9]:
import copy

In [10]:
d = new_dynamics(op, ma)

In [11]:
# %%timeit
# start = time.time()
acting_list = op._acting_on[:,1:3]
w_ = ma._w[acting_list]
x = np.zeros((9,2))

n = 0
for i in range(3):
    for j in range(3):

        x[n,1] = 2*(j-1)
        x[n,0] = 2*(i-1)
        n += 1
r_primes = np.einsum('ij,kjl->kil', x, w_)
e = np.exp(r_primes)
c_r = (e + 1/e)/2
s_r = (e - 1/e)/2
# print(time.time()-start)

In [12]:
sweep_size = 400
sa_mul = nk.sampler.DimerMetropolisLocal_multi(machine=ma, op=op_transition, length = length, n_chains=n_chains, sweep_size = sweep_size, kernel = 1, n_jobs=12)
sa_mul.reset()
# sa_mul.sa_list[0]._state

number of core : 12


In [13]:
# sa_mul.discard(100)
sa_mul.reset()
n_discard = 100
sa_mul.sa_list[0]._state
discard_sample = sa_mul.discard(n_discard)

In [14]:
s = time.time()
samples_state = sa_mul.generate_samples(10**4)
samples_state = samples_state.reshape(-1,samples_state.shape[-1])
print(time.time()-s)

19.225148916244507


In [43]:
import mkl
import time
mkl.set_num_threads(12)
reload(utils)

<module 'scripts.utils' from '/home/keisuke/Documents/Research/sshfs/DimerMaster/scripts/utils.py'>

In [46]:
ma._ws.shape

(288, 1)

In [44]:
x = samples_state.astype(np.int8)[:int(10000)]
import numpy as _np
utils.der_log(x, ma._ws, ma._autom, ma._z2)
# %time ma.der_log(x)

     der_log 2.8346543312072754


array([[ 5.740161  , 12.744009  ,  3.0533211 , ...,  5.5768757 ,
         0.28405055, 12.062937  ],
       [-3.4449987 ,  3.5930848 ,  3.9339056 , ...,  6.1747303 ,
        -1.1082885 ,  6.4693832 ],
       [11.599756  , 25.382332  , 11.2740555 , ..., 25.00316   ,
         7.6491594 , 28.22224   ],
       ...,
       [ 1.2168527 , 16.676601  ,  4.222075  , ..., 10.280554  ,
         0.05059814, 14.95392   ],
       [-3.9689238 ,  4.2751436 ,  1.611721  , ..., -1.0778625 ,
        -5.0124445 ,  3.522859  ],
       [-0.6613717 ,  2.516026  , -1.1257331 , ..., -0.04596555,
        -1.5139108 ,  3.6921132 ]], dtype=float32)

In [41]:
import dask.array as da

In [42]:
x = da.from_array(x, chunks=(1000, 1000))

TypeError: 'module' object is not callable

In [33]:
utils.mul_p(ma, x, 6)

     der_log     der_log  0.88973975181579590.9100797176361084

     der_log 0.905550479888916
     der_log 0.9194719791412354
     der_log 0.8855631351470947
     der_log 0.9439022541046143


In [115]:
x = samples_state.astype(np.int8)[:int(10000)]
%time out = utils.mul(ma, x, 12)

     der_log     der_log 0.7167143821716309 
0.7106835842132568
     der_log 0.7147536277770996
     der_log 0.7327902317047119
     der_log 0.7046256065368652
     der_log 0.6488778591156006
     der_log 0.7679393291473389
     der_log 0.7096126079559326
     der_log 0.6942884922027588
     der_log 0.650707483291626
     der_log 0.6366190910339355
     der_log 0.7044930458068848
CPU times: user 31.5 ms, sys: 176 ms, total: 207 ms
Wall time: 834 ms


In [108]:
symm_num = ma._autom.shape[0]
half_symm_num = int(symm_num/2)
batch_size = x.shape[0]
s = time.time()
ws2 = ma._ws.astype(_np.float32)  * 2
ws = ma._ws.astype(_np.float32) 
# T_x_1 = _np.empty((x.shape[0], half_symm_num, x.shape[1]), dtype=_np.float32)
# T_x_2 = _np.empty_like(T_x_1)
# T_x_1[:,:,:] = ma.translate_x(x, ma._autom[:half_symm_num])
# T_x_2[:,:,:] = ma.translate_x(x * ma._z2[1], ma._autom[half_symm_num:])

T_x_1 = ma.translate_x(x, ma._autom[:half_symm_num]).astype(np.float32)
T_x_2 = ma.translate_x(x * ma._z2[1], ma._autom[half_symm_num:]).astype(np.float32)


print('     matmal', time.time()-s)
# e1 = np.exp(T_x_1.dot(ws2))
# e2 = np.exp(T_x_2.dot(ws2))
# tanh_1 = (e1-1)/(e1+1)
# tanh_2 = (e2-1)/(e2+1)
tanh_1 = _np.tanh(T_x_1.astype(_np.float32).dot(ws))
tanh_2 = _np.tanh(T_x_2.astype(_np.float32).dot(ws))

print('     cal tan', time.time()-s)
out1 = _np.einsum('ijk,ijl->ikl',T_x_1, tanh_1)
out = (out1 + _np.einsum('ijk,ijl->ikl',T_x_2, tanh_2)).reshape(batch_size,-1)
print('     cal output', time.time()-s)

     matmal 0.5909111499786377
     cal tan 2.1211133003234863
     cal output 3.3944082260131836


In [109]:
out

array([[ 5.740161  , 12.744009  ,  3.0533211 , ...,  5.5768757 ,
         0.28405055, 12.062937  ],
       [-3.4449987 ,  3.5930848 ,  3.9339056 , ...,  6.1747303 ,
        -1.1082885 ,  6.4693832 ],
       [11.599756  , 25.382332  , 11.2740555 , ..., 25.00316   ,
         7.6491594 , 28.22224   ],
       ...,
       [ 1.2168527 , 16.676601  ,  4.222075  , ..., 10.280554  ,
         0.05059814, 14.95392   ],
       [-3.9689238 ,  4.2751436 ,  1.611721  , ..., -1.0778625 ,
        -5.0124445 ,  3.522859  ],
       [-0.6613717 ,  2.516026  , -1.1257331 , ..., -0.04596555,
        -1.5139108 ,  3.6921132 ]], dtype=float32)

In [88]:
mkl.set_num_threads(12)

12

In [94]:
%time _np.einsum('ijk,ijl->ikl',T_x_1, tanh_1,optimize=True)

CPU times: user 635 ms, sys: 3.56 ms, total: 638 ms
Wall time: 638 ms


array([[[ 6.9673934 ],
        [ 7.6223764 ],
        [ 2.871721  ],
        ...,
        [ 2.0493302 ],
        [ 0.3213613 ],
        [ 6.2431655 ]],

       [[-1.9632264 ],
        [ 1.9563326 ],
        [ 3.3092232 ],
        ...,
        [ 4.1621113 ],
        [ 2.881228  ],
        [ 3.4615865 ]],

       [[ 5.3315783 ],
        [12.185754  ],
        [ 4.155278  ],
        ...,
        [11.887801  ],
        [ 4.8729267 ],
        [16.132814  ]],

       ...,

       [[ 0.7106112 ],
        [ 6.2356653 ],
        [ 4.512728  ],
        ...,
        [ 2.8518093 ],
        [ 1.8645495 ],
        [ 8.467565  ]],

       [[-1.0192873 ],
        [-0.6533693 ],
        [-0.28084058],
        ...,
        [-0.13933605],
        [-1.861416  ],
        [ 2.5427675 ]],

       [[ 1.2401958 ],
        [ 4.221634  ],
        [ 0.65432435],
        ...,
        [ 1.3101027 ],
        [ 1.8859015 ],
        [ 4.1175203 ]]], dtype=float32)

In [92]:
%time np.matmul(a,b)

CPU times: user 641 ms, sys: 75.7 ms, total: 717 ms
Wall time: 717 ms


array([[[ 6.967391  ],
        [ 7.6223764 ],
        [ 2.8717208 ],
        ...,
        [ 2.0493302 ],
        [ 0.32136142],
        [ 6.243164  ]],

       [[-1.9632276 ],
        [ 1.9563335 ],
        [ 3.3092234 ],
        ...,
        [ 4.1621103 ],
        [ 2.8812284 ],
        [ 3.461585  ]],

       [[ 5.331578  ],
        [12.185753  ],
        [ 4.155279  ],
        ...,
        [11.887802  ],
        [ 4.8729267 ],
        [16.132816  ]],

       ...,

       [[ 0.71061194],
        [ 6.235666  ],
        [ 4.5127287 ],
        ...,
        [ 2.8518093 ],
        [ 1.8645493 ],
        [ 8.467566  ]],

       [[-1.0192869 ],
        [-0.65336955],
        [-0.28084075],
        ...,
        [-0.13933638],
        [-1.8614167 ],
        [ 2.542767  ]],

       [[ 1.2401961 ],
        [ 4.221635  ],
        [ 0.6543241 ],
        ...,
        [ 1.3101027 ],
        [ 1.8859015 ],
        [ 4.1175213 ]]], dtype=float32)

In [74]:
a = T_x_1.transpose((0,2,1))

In [83]:
b = (tanh_1).transpose(0,1,2)

In [84]:
b.shape

(9996, 144, 1)

In [86]:
np.matmul(a,b).shape

(9996, 288, 1)

In [87]:
out1.shape

(9996, 288, 1)

In [37]:
einsum(T_x_1, tanh_1)-np.einsum('ijk,ijl->ikl',T_x_1, tanh_1)

array([[[-1.77635684e-15],
        [ 1.77635684e-15],
        [ 0.00000000e+00],
        ...,
        [ 3.55271368e-15],
        [ 3.55271368e-15],
        [ 1.33226763e-15]],

       [[ 4.44089210e-16],
        [ 4.44089210e-16],
        [-4.44089210e-16],
        ...,
        [-1.77635684e-15],
        [ 1.77635684e-15],
        [ 0.00000000e+00]],

       [[ 1.11022302e-16],
        [-2.22044605e-16],
        [ 3.60822483e-16],
        ...,
        [ 5.32907052e-15],
        [ 0.00000000e+00],
        [ 3.55271368e-15]],

       ...,

       [[-1.11022302e-15],
        [ 1.77635684e-15],
        [-1.77635684e-15],
        ...,
        [-1.77635684e-15],
        [-1.77635684e-15],
        [-4.44089210e-16]],

       [[ 2.22044605e-16],
        [-2.66453526e-15],
        [ 3.55271368e-15],
        ...,
        [ 7.10542736e-15],
        [-8.88178420e-16],
        [ 5.32907052e-15]],

       [[ 2.22044605e-15],
        [-8.88178420e-16],
        [ 3.55271368e-15],
        ...,
        

In [19]:
import math

import netket as _nk
import numpy as _np

from netket.operator import local_values as _local_values
from netket.stats import (
    statistics as _statistics,
    mean as _mean,
    sum_inplace as _sum_inplace,
)

from netket.vmc_common import info, tree_map
from netket.abstract_variational_driver import AbstractVariationalDriver
import time
import multiprocessing as mp
import copy

In [20]:
class Vmc(AbstractVariationalDriver):
    """
    Energy minimization using Variational Monte Carlo (VMC).
    """

    def __init__(
        self, hamiltonian, sampler, optimizer, n_samples, n_discard=None, sr=None
    ):
        """
        Initializes the driver class.

        Args:
            hamiltonian (AbstractOperator): The Hamiltonian of the system.
            sampler: The Monte Carlo sampler.
            optimizer (AbstractOptimizer): Determines how optimization steps are performed given the
                bare energy gradient.
            n_samples (int): Number of Markov Chain Monte Carlo sweeps to be
                performed at each step of the optimization.
            n_discard (int, optional): Number of sweeps to be discarded at the
                beginning of the sampling, at each step of the optimization.
                Defaults to 10% of the number of samples allocated to each MPI node.
            sr (SR, optional): Determines whether and how stochastic reconfiguration
                is applied to the bare energy gradient before performing applying
                the optimizer. If this parameter is not passed or None, SR is not used.

        Example:
            Optimizing a 1D wavefunction with Variational Monte Carlo.

            >>> import netket as nk
            >>> SEED = 3141592
            >>> g = nk.graph.Hypercube(length=8, n_dim=1)
            >>> hi = nk.hilbert.Spin(s=0.5, graph=g)
            >>> ma = nk.machine.RbmSpin(hilbert=hi, alpha=1)
            >>> ma.init_random_parameters(seed=SEED, sigma=0.01)
            >>> ha = nk.operator.Ising(hi, h=1.0)
            >>> sa = nk.sampler.MetropolisLocal(machine=ma)
            >>> op = nk.optimizer.Sgd(learning_rate=0.1)
            >>> vmc = nk.Vmc(ha, sa, op, 200)

        """
        super(Vmc, self).__init__(
            sampler.machine, optimizer, minimized_quantity_name="Energy"
        )

        self._ham = hamiltonian
        self._sampler = sampler
        self.sr = sr

        self._npar = self._machine.n_par

        self._batch_size = sampler.sample_shape[0]

        # Check how many parallel nodes we are running on
        self.n_nodes = _nk.utils.n_nodes

        self.n_samples = n_samples
        self.n_discard = n_discard

        self._dp = None

    @property
    def sr(self):
        return self._sr

    @sr.setter
    def sr(self, sr):
        self._sr = sr
        if self._sr is not None:
            self._sr.setup(self.machine)

    @property
    def n_samples(self):
        return self._n_samples

    @n_samples.setter
    def n_samples(self, n_samples):
        if n_samples <= 0:
            raise ValueError(
                "Invalid number of samples: n_samples={}".format(n_samples)
            )

        n_samples_chain = int(math.ceil((n_samples / self._batch_size)))
        self._n_samples_node = int(math.ceil(n_samples_chain / self.n_nodes))

        self._n_samples = int(self._n_samples_node * self._batch_size * self.n_nodes)

        self._samples = None

        self._grads = None
        self._jac = None

    @property
    def n_discard(self):
        return self._n_discard

    @n_discard.setter
    def n_discard(self, n_discard):
        if n_discard is not None and n_discard < 0:
            raise ValueError(
                "Invalid number of discarded samples: n_discard={}".format(n_discard)
            )
        self._n_discard = (
            int(n_discard)
            if n_discard != None
            else self._n_samples_node * self._batch_size // 10
        )

        print('discard = ',self._n_discard)

    def _forward_and_backward(self):
        """
        Performs a number of VMC optimization steps.

        Args:
            n_steps (int): Number of steps to perform.
        """

        self._sampler.reset()

        # Burnout phase


        print('n_discard = ',self._n_discard)
        s = time.time()
        self._sampler.discard(self._n_discard)
        print('discard samples', time.time()-s)

        # Generate samples and store them
        print('n_samples_node = ',self._n_samples_node)

        s = time.time()
        self._samples = self._sampler.generate_samples(
            self._n_samples_node, samples=self._samples
        )
        print('generate_samples : ',time.time()-s)


        # print(hexagon.is_dimer_basis2(self._samples[0]))

        # print(self._samples.shape)

        # Compute the local energy estimator and average Energy
        # print(whoami(), whosdaddy())

        s = time.time()
        eloc, self._loss_stats = self._get_mc_stats(self._ham)
        print('get_mc_stats', time.time()-s)

        # Center the local energy
        eloc -= _mean(eloc)

        samples_r = self._samples.reshape((-1, self._samples.shape[-1]))
        eloc_r = eloc.reshape(-1, 1)

        # Perform update

        if self._sr:
            s = time.time()
            # When using the SR (Natural gradient) we need to have the full jacobian


            # self._grads, self._jac = self._machine.vector_jacobian_prod(
            #     samples_r.astype(_np.int8), eloc_r / self._n_samples, self._grads, return_jacobian=True
            # )
            # 
            # s = time.time()


            self._grads, self._jac = self.SR_process_mul(samples_r.astype(_np.int8), eloc_r)

            # grads, jac = self.SR_process(samples_r.astype(_np.int8), eloc_r)

            # print(self._grads - grads)
            # print(self._jac - jac )
            print('--->> cal O and jac ', time.time()-s)

            self._grads = tree_map(_sum_inplace, self._grads)

            self._dp = self._sr.compute_update(self._jac, self._grads, self._dp)
            print('compute_update ', time.time()-s)

        else:
            # Computing updates using the simple gradient
            self._grads = self._machine.vector_jacobian_prod(
                samples_r, eloc_r / self._n_samples, self._grads
            )

            self._grads = tree_map(_sum_inplace, self._grads)

            #  if Real pars but complex gradient, take only real part
            # not necessary for SR because sr already does it.
            if not self._machine.has_complex_parameters:
                self._dp = tree_map(lambda x: x.real, self._grads)
            else:
                self._dp = self._grads

        return self._dp

    @property
    def energy(self):
        """
        Return MCMC statistics for the expectation value of observables in the
        current state of the driver.
        """
        return self._loss_stats

    def _estimate_stats(self, obs):
        return self._get_mc_stats(obs)[1]

    def reset(self):
        self._sampler.reset()
        super().reset()

    def _get_mc_stats(self, op):


        samples_r = self._samples.reshape((-1, self._samples.shape[-1]))
        # print(whoami(), whosdaddy(), hexagon.is_dimer_basis2(samples_r).all(), samples_r.shape)

        loc = _local_values(op, self._machine, samples_r).reshape(
            self._samples.shape[0:2]
        )

        # notice that loc.T is passed to statistics, since that function assumes
        # that the first index is the batch index.
        return loc, _statistics(loc.T)

    def __repr__(self):
        return "Vmc(step_count={}, n_samples={}, n_discard={})".format(
            self.step_count, self.n_samples, self.n_discard
        )

    def info(self, depth=0):
        lines = [
            "{}: {}".format(name, info(obj, depth=depth + 1))
            for name, obj in [
                ("Hamiltonian ", self._ham),
                ("Machine     ", self._machine),
                ("Optimizer   ", self._optimizer),
                ("SR solver   ", self._sr),
            ]
        ]
        return "\n{}".format(" " * 3 * (depth + 1)).join([str(self)] + lines)

    def SR_process(self, samples, eloc):
        n_samples = eloc.shape[0]

        grads, jac =  self._machine.vector_jacobian_prod(
                samples.astype(_np.int8), eloc/n_samples, return_jacobian=True
            )

        print(grads, jac)

        return grads, jac

    
    @staticmethod
    def run_(ma, samples, eloc, qout):
        try:
            s = time.time()
            n_samples = eloc.shape[0]

            out =  ma.vector_jacobian_prod(
                    samples.astype(_np.int8), eloc/n_samples, return_jacobian=True
                )
            # print('cal jacobian', time.time()-s)
            
            # out = vmc.SR_process(samples, eloc)
            qout.put(out)
        
        except KeyboardInterrupt:
            print('Received keyboardinterrupt\n')
            qout.put(None)

    def SR_process_mul(self, samples, eloc):
        queue = []
        process = []
        n_samples = samples.shape[0]
        n_each = int(n_samples/self._sampler.n_jobs)
        # print(eloc)
        for i in range(self._sampler.n_jobs):
            queue.append(mp.Queue())
            sample_r = samples[i*n_each : (i+1) * n_each].copy()
            eloc_r = eloc[i*n_each : (i+1) * n_each].copy()
            p = mp.Process(target=self.run_, args=(self._machine, sample_r, eloc_r ,queue[i]))
            # out = self.run_(copy.copy(self._machine), sample_r, eloc_r , None)
            p.start()
            process.append(p)
        
        
        out1 = []
        out2 = []

        for i in range(self._sampler.n_jobs):
            temp_out = queue[i].get()

            if temp_out is not None:
                out1.append(temp_out[0])
                out2.append(temp_out[1])
            else:
                raise NameError('keyboardinterrupt')
        
        # print('# of accepted samples',self.sa_list[0]._accepted_samples)

        
        return _np.stack(out1).mean(axis=0), _np.vstack(out2)


In [21]:
sweep_size = 10
sa_mul = nk.sampler.DimerMetropolisLocal_multi(machine=ma, op=op_transition, length = length, n_chains=n_chains, sweep_size = sweep_size, kernel = 1, n_jobs=12)
sa_mul.reset()
sr = nk.optimizer.SR(ma, diag_shift=1e-2)
opt = nk.optimizer.Sgd(ma, learning_rate=0.05, decay_factor = 1 ,N = 100)
gs = Vmc(
    hamiltonian=op,
    sampler=sa_mul,
    optimizer=opt,
    n_samples=10000,
    sr = sr,
    n_discard = 300,
    )

number of core : 12
discard =  300


In [22]:
gs._forward_and_backward()

n_discard =  300
discard samples 0.2670154571533203
n_samples_node =  10000
generate_samples :  0.7546594142913818
     prepare getting local values 0.08658385276794434
     obtained local values 1.3473169803619385
get_mc_stats 1.9718549251556396
     matmal
 0.03272366523742676     matmal      matmal 0.03778052330017090.040091514587402344

     matmal 0.04631853103637695
     matmal 0.04709959030151367
     matmal 0.04075455665588379     matmal     matmal 
 0.081640481948852540.055818796157836914

     matmal 0.0637660026550293
     matmal 0.08003687858581543
     matmal 0.0761115550994873
     matmal 0.07736015319824219
     cal tan 0.5424959659576416
     cal tan 0.5780601501464844
     cal tan 0.5024044513702393
     cal tan 0.5611164569854736
     cal tan 0.5080375671386719
     cal tan 0.5865755081176758
     cal tan 0.52020263671875
     cal tan 0.5704858303070068     cal tan
 0.5084266662597656
     cal tan 0.4849052429199219
     cal tan 0.5242774486541748
     cal tan 0.49657

array([ 1.10662582e-02+0.j, -3.42723800e-02+0.j, -2.71651158e-02+0.j,
        1.53122570e-02+0.j, -1.47593259e-02+0.j,  4.15055189e-02+0.j,
       -1.81942111e-02+0.j,  1.09686842e-02+0.j,  3.28631120e-03+0.j,
        3.43992962e-02+0.j,  3.39389839e-03+0.j,  1.40793114e-03+0.j,
        1.62267183e-02+0.j,  1.59245606e-02+0.j,  6.29272936e-03+0.j,
       -2.80281271e-04+0.j, -2.80510750e-02+0.j, -4.02010989e-03+0.j,
        2.55178322e-02+0.j,  2.10687331e-02+0.j, -2.02456770e-02+0.j,
        1.58886988e-02+0.j, -3.44110354e-03+0.j,  3.83070465e-03+0.j,
       -4.03990412e-02+0.j,  3.65752078e-02+0.j, -7.40568875e-03+0.j,
       -2.35022587e-03+0.j, -2.72309336e-02+0.j,  1.92970242e-03+0.j,
        2.83542511e-02+0.j, -2.42808434e-03+0.j,  1.27571328e-02+0.j,
       -1.86308339e-02+0.j, -8.46665236e-03+0.j,  1.12230737e-02+0.j,
        2.03704258e-02+0.j, -3.44201679e-02+0.j,  2.75484515e-03+0.j,
       -1.55486725e-02+0.j,  1.75853590e-02+0.j,  1.99994555e-03+0.j,
        2.38679697e-

In [32]:
@njit
def translate_x(x, autom):

    out = np.empty((x.shape[0], autom.shape[0], x.shape[1]), dtype=x.dtype)
    for l in range(x.shape[0]):
        out_l = out[l]
        x_l = x[l]
        for i in range(autom.shape[0]):
            for j in range(x.shape[1]):
                out_l[i, j] = x_l[autom[i, j]]
    return out


In [24]:
x = x.astype(np.int8)

In [37]:
%%time 
x_t = x.T.copy()
out = x_t[ma._autom]
out = out.transpose((2,0,1))

CPU times: user 32.6 ms, sys: 71.7 ms, total: 104 ms
Wall time: 103 ms


In [34]:
(out.transpose((2,0,1)) == translate_x(x, ma._autom)).all()

True

In [35]:
%time translate_x(x, ma._autom)

CPU times: user 398 ms, sys: 108 ms, total: 506 ms
Wall time: 505 ms


array([[[ 1, -1, -1, ...,  1,  1, -1],
        [-1, -1,  1, ..., -1, -1, -1],
        [ 1, -1,  1, ..., -1,  1, -1],
        ...,
        [-1,  1,  1, ..., -1, -1, -1],
        [ 1,  1,  1, ..., -1, -1, -1],
        [ 1,  1, -1, ..., -1, -1, -1]],

       [[-1, -1, -1, ..., -1, -1, -1],
        [-1, -1, -1, ..., -1,  1,  1],
        [-1, -1,  1, ...,  1,  1, -1],
        ...,
        [-1, -1, -1, ..., -1, -1, -1],
        [-1,  1,  1, ..., -1, -1,  1],
        [ 1,  1, -1, ...,  1, -1, -1]],

       [[-1, -1, -1, ..., -1, -1,  1],
        [-1, -1, -1, ...,  1,  1,  1],
        [-1, -1,  1, ...,  1,  1,  1],
        ...,
        [ 1, -1, -1, ..., -1, -1, -1],
        [-1, -1,  1, ..., -1,  1,  1],
        [ 1,  1, -1, ...,  1,  1,  1]],

       ...,

       [[ 1, -1,  1, ...,  1, -1, -1],
        [ 1, -1, -1, ..., -1, -1, -1],
        [-1, -1, -1, ..., -1, -1, -1],
        ...,
        [-1, -1, -1, ..., -1, -1, -1],
        [-1, -1, -1, ..., -1, -1, -1],
        [-1,  1,  1, ..., -1, -1

In [2]:
%timeit translate_x(x_t, ma._autom)

NameError: name 'translate_x' is not defined

In [103]:
out = (out1 + _np.einsum('ijk,ijl->ikl',T_x_2, tanh_2)).reshape(batch_size,-1)

array([0.09045485+0.j, 0.13306426+0.j, 0.05478006+0.j, ...,
       0.09657571+0.j, 0.10611624+0.j, 0.04028375+0.j])

In [104]:
ma.log_val(samples_state)

array([0.09045485+0.j, 0.13306426+0.j, 0.05478006+0.j, ...,
       0.09657571+0.j, 0.10611624+0.j, 0.04028375+0.j])

In [63]:
P = hex_.autom(reverse=True, half=True)[0][1]
z2 = hex_.autom(reverse=True, half=True)[1][1]

In [28]:
@njit
def translate_x_z2(x, autom, z2):
    
    out = np.empty((x.shape[0], autom.shape[0], x.shape[1]), dtype=x.dtype)
    
    for i in range(autom.shape[0]):
        
        z2_i = z2[i // int(autom.shape[0]/2)]
        for j in range(x.shape[1]):
            z2_i_j = z2_i[j]
            for l in range(x.shape[0]):
            

                        
                out[l, i, j] = x[l, autom[i, j]] * z2_i_j
    return out
@njit
def translate_x(x, autom):
    
    out = np.empty((x.shape[0], autom.shape[0], x.shape[1]), dtype=x.dtype)
    for l in range(x.shape[0]):
        out_l = out[l]
        x_l = x[l]
        for i in range(autom.shape[0]):
            for j in range(x.shape[1]):
                out_l[i, j] = x_l[autom[i, j]]
    return out

In [41]:
out = translate_x(samples_state, ma._autom)

In [47]:
tanh_1 = np.tanh(out[:,:16,:].dot(ma._ws))

In [48]:
tanh_2 = np.tanh(out[:,16:,:].dot(ma._ws * ma._z2[1].reshape(-1,1)))

In [ ]:
np.einsum('ijk,ijl->ikl',T_x, tanh).reshape(batch_size,-1)

In [34]:
%timeit out[:, :16, :]

180 ns ± 2.19 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)


In [31]:
%timeit samples_state[:, ma._autom]

1.26 ms ± 4.19 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)


In [49]:
samples_state * ma._z2[1]

array([[ 1.,  1., -1., ..., -1., -1.,  1.],
       [ 1.,  1., -1., ..., -1., -1.,  1.],
       [-1.,  1.,  1., ..., -1.,  1.,  1.],
       ...,
       [-1., -1., -1., ..., -1., -1.,  1.],
       [-1., -1., -1., ...,  1., -1.,  1.],
       [ 1., -1., -1., ...,  1., -1., -1.]])

In [450]:
samples_state[:, ma._autom].shape

(99996, 16, 32)

In [438]:
%%timeit
    A = samples_state[:,P1]
    B = samples_state[:,P2] * z2

300 ms ± 7.8 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [424]:
%timeit np.concatenate((samples_state[:,P1], (samples_state * z2_2)[:,P2]), axis=1)

413 ms ± 81 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [418]:
%timeit (samples_state * z2_2)[:,P2]

121 ms ± 716 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [420]:
(samples_state * z2_2)[:,P2].shape

(99996, 16, 32)

In [419]:
%timeit (samples_state[:,P1])

117 ms ± 2.93 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [421]:
(samples_state[:,P2]).shape

(99996, 16, 32)

In [402]:
P1 = hex_.autom(reverse=True, half=True)[0][0]
P2 = hex_.autom(reverse=True, half=True)[0][1]

z2_1 = hex_.autom(reverse=True, half=True)[1][0]
z2_2 = hex_.autom(reverse=True, half=True)[1][1]

In [398]:
(ma.log_val(np.ones(32).reshape(1,-1)))

array([18.78037962+0.j])

In [400]:
ma.log_val(np.ones(32).reshape(1,-1)[:,P[0]] * z2)

array([19.10261654+0.j])

In [351]:
np.exp(ma.log_val(samples_state[1][P] * z2))

array([91882120.22446366+0.j, 91882120.22446397+0.j,
       91882120.22446397+0.j, 91882120.22446397+0.j,
       91882120.22446397+0.j, 91882120.22446366+0.j,
       91882120.22446366+0.j, 91882120.22446333+0.j,
       91882120.22446397+0.j, 91882120.22446366+0.j,
       91882120.22446366+0.j, 91882120.22446333+0.j,
       91882120.22446366+0.j, 91882120.22446397+0.j,
       91882120.22446397+0.j, 91882120.22446397+0.j])

In [331]:
samples_state[0][P[0].reshape(1,-1)] * z2

array([[ 1.,  1.,  1.,  1.,  1.,  1.,  1.,  1.,  1.,  1., -1.,  1.,  1.,
         1., -1.,  1., -1.,  1.,  1.,  1., -1.,  1.,  1.,  1.,  1.,  1.,
         1.,  1.,  1.,  1.,  1.,  1.]])

In [239]:
l = []
for n in range(100):
    test = (samples_state[n][P[0].reshape(1,-1)] * z2)
    l.append(ma.log_val(samples_state[n].reshape(1,-1))-ma.log_val(test))
#     print(l[n])
np.mean(l)

(0.0011174457896773549+0j)

In [ ]:
x = 

In [240]:
state = ma.to_array()

In [204]:
np.abs(1-np.exp(ma.log_val(samples_state))/np.exp(ma.log_val(samples_state))[0])

array([0.00000000e+00, 2.03207674e-03, 3.13083279e-03, 3.56067447e-03,
       6.58319363e-03, 8.67622928e-03, 2.03207674e-03, 8.92931067e-03,
       8.92931067e-03, 1.36442176e-02, 6.98818363e-03, 6.98818363e-03,
       6.98818363e-03, 3.13083279e-03, 3.13083279e-03, 1.36442176e-02,
       2.03207674e-03, 2.03207674e-03, 6.98818363e-03, 6.58319363e-03,
       6.98818363e-03, 2.22044605e-16, 1.36442176e-02, 6.98818363e-03,
       6.58319363e-03, 6.98818363e-03, 0.00000000e+00, 0.00000000e+00,
       8.92931067e-03, 3.13083279e-03, 2.03207674e-03, 6.58319363e-03,
       8.92931067e-03, 3.13083279e-03, 6.58319363e-03, 1.36442176e-02,
       6.98818363e-03, 3.13083279e-03, 1.36442176e-02, 1.15435058e-02,
       6.98818363e-03, 6.58319363e-03, 8.92931067e-03, 6.98818363e-03,
       8.92931067e-03, 1.36442176e-02, 6.98818363e-03, 0.00000000e+00,
       6.58319363e-03, 1.36442176e-02, 1.15435058e-02, 1.09805986e-02,
       6.58319363e-03, 0.00000000e+00, 1.15435058e-02, 8.67622928e-03,
      

In [84]:
x[:,P][:,0] * z2

array([[ 1.,  1.,  1.,  1.,  1.,  1.,  1.,  1., -1., -1., -1., -1., -1.,
        -1., -1., -1.,  1.,  1.,  1.,  1.,  1.,  1.,  1.,  1., -1., -1.,
        -1., -1., -1., -1., -1., -1.]])

In [42]:
hex_.is_dimer_basis(samples_state[n][P] * z2)

array([ True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True])

In [35]:
sections = np.zeros(samples_state.shape[0], dtype=np.int64)
op.get_conn_flattened(samples_state, sections)

(array([[ 1,  1,  1, ..., -1, -1, -1],
        [ 1, -1,  1, ..., -1, -1, -1],
        [ 1,  1,  1, ..., -1, -1, -1],
        ...,
        [-1,  1,  1, ...,  1, -1, -1],
        [-1,  1,  1, ...,  1, -1, -1],
        [-1,  1, -1, ...,  1,  1, -1]], dtype=int8),
 array([ 3. +0.j, -1.1+0.j, -1.1+0.j, ..., -1.1+0.j, -1.1+0.j, -1.1+0.j]))

In [120]:
np.max(sections[1:]-sections[:-1])

In [121]:
sections

In [122]:
samples_state = sa_mul.generate_samples(10**5)

In [29]:
samples_state = samples_state.reshape(-1,samples_state.shape[-1])

In [30]:
from scripts import new_dynamics
d = new_dynamics(op, ma)

In [31]:
%time d.multiprocess(samples_state, 100, n = 12)

CPU times: user 131 ms, sys: 470 ms, total: 600 ms
Wall time: 5.91 s


(array([[[-1, -1, -1, ..., -1, -1, -1],
         [-1, -1, -1, ..., -1, -1, -1],
         [-1, -1, -1, ..., -1, -1, -1],
         ...,
         [ 1, -1, -1, ..., -1,  1,  1],
         [ 1, -1, -1, ..., -1,  1,  1],
         [ 1,  1, -1, ...,  1,  1,  1]],
 
        [[-1, -1,  1, ..., -1, -1, -1],
         [-1, -1, -1, ..., -1, -1, -1],
         [-1, -1, -1, ..., -1, -1, -1],
         ...,
         [ 1, -1, -1, ..., -1,  1,  1],
         [ 1, -1, -1, ..., -1,  1,  1],
         [ 1, -1, -1, ..., -1,  1,  1]],
 
        [[-1, -1,  1, ..., -1, -1, -1],
         [-1, -1, -1, ..., -1, -1, -1],
         [-1, -1, -1, ..., -1, -1, -1],
         ...,
         [ 1,  1, -1, ...,  1,  1,  1],
         [ 1, -1, -1, ..., -1,  1,  1],
         [ 1, -1, -1, ..., -1,  1,  1]],
 
        ...,
 
        [[-1, -1,  1, ..., -1, -1,  1],
         [ 1,  1,  1, ...,  1, -1, -1],
         [-1, -1, -1, ...,  1,  1,  1],
         ...,
         [-1,  1, -1, ...,  1,  1,  1],
         [-1, -1, -1, ...,  1,  1,  1],


In [32]:
g = nk.graph.Graph(nodes = [i for i in range(length[0] * length[1] * 2)])
hi = nk.hilbert.Spin(s=0.5, graph=g)
hex_ = nk.machine.new_hex(np.array(length))


l = []
for i in range(length[0]):
    for j in range(length[1]):
        l.append([i, j])
l = np.array(l)
a = 0
a_ = [a for _ in range(np.prod(length))]
a = np.array(a_)



edges, colors = hex_.dimer_corr(l,a)
operators = f.return_dimer_operator(hi, edges, colors)

# calculate autocorrelation

In [33]:
sections = np.zeros(samples_state.shape[0])
num_flippable = np.zeros_like(sections)
for i in range(len(operators)):
    num_flippable += operators[i].get_conn_flattened(samples_state, sections)[1].real

In [28]:
num_flippable_mean = num_flippable.mean()
num_flippable_prime = num_flippable-num_flippable_mean

In [29]:
num = 1000
auto_corr = np.zeros(num)
for i in range(num):
    auto_corr[i] = (num_flippable_prime[(i+1):] * num_flippable_prime[:-(i+1)]).mean()

In [30]:
from plotly import graph_objects as go

fig = go.Figure()
fig.add_trace(
    go.Scatter(x=np.arange(num-1), y =auto_corr[1:]-auto_corr[:-1])
)
fig.show()

## estimate number of discard

In [37]:
m = num_flippable[10**5:].mean()
for i in range(10**5):
    print(num_flippable[i:i+10**5].mean()-m, '####', i)

0.07601999999999975 #### 0
0.07597999999999949 #### 1
0.07597999999999949 #### 2
0.07599999999999874 #### 3
0.07599999999999874 #### 4
0.07599999999999874 #### 5
0.07599999999999874 #### 6
0.07597999999999949 #### 7
0.07597999999999949 #### 8
0.07599999999999874 #### 9
0.076039999999999 #### 10
0.076039999999999 #### 11
0.07606000000000002 #### 12
0.07607999999999926 #### 13
0.07610000000000028 #### 14
0.07613999999999876 #### 15
0.07621999999999929 #### 16
0.07625999999999955 #### 17
0.0762799999999988 #### 18
0.07625999999999955 #### 19
0.07625999999999955 #### 20
0.07629999999999981 #### 21
0.07634000000000007 #### 22
0.07639999999999958 #### 23
0.07641999999999882 #### 24
0.07641999999999882 #### 25
0.07643999999999984 #### 26
0.07643999999999984 #### 27
0.07643999999999984 #### 28
0.07641999999999882 #### 29
0.07638000000000034 #### 30
0.07638000000000034 #### 31
0.07639999999999958 #### 32
0.07638000000000034 #### 33
0.07634000000000007 #### 34
0.07631999999999906 #### 35
0.07631

0.07362000000000002 #### 1647
0.07355999999999874 #### 1648
0.07352000000000025 #### 1649
0.07347999999999999 #### 1650
0.07345999999999897 #### 1651
0.07343999999999973 #### 1652
0.07338000000000022 #### 1653
0.07333999999999996 #### 1654
0.07325999999999944 #### 1655
0.07319999999999993 #### 1656
0.07314000000000043 #### 1657
0.07307999999999915 #### 1658
0.07303999999999888 #### 1659
0.07296000000000014 #### 1660
0.07286000000000037 #### 1661
0.07273999999999958 #### 1662
0.0726199999999988 #### 1663
0.07251999999999903 #### 1664
0.07245999999999952 #### 1665
0.07240000000000002 #### 1666
0.072379999999999 #### 1667
0.07235999999999976 #### 1668
0.07233999999999874 #### 1669
0.0723199999999995 #### 1670
0.0723199999999995 #### 1671
0.07233999999999874 #### 1672
0.072379999999999 #### 1673
0.07240000000000002 #### 1674
0.07244000000000028 #### 1675
0.07245999999999952 #### 1676
0.07247999999999877 #### 1677
0.07245999999999952 #### 1678
0.07245999999999952 #### 1679
0.072440000000000

0.07685999999999993 #### 3431
0.07699999999999996 #### 3432
0.07713999999999999 #### 3433
0.07723999999999975 #### 3434
0.07732000000000028 #### 3435
0.07735999999999876 #### 3436
0.07737999999999978 #### 3437
0.07737999999999978 #### 3438
0.07735999999999876 #### 3439
0.07735999999999876 #### 3440
0.07733999999999952 #### 3441
0.07735999999999876 #### 3442
0.07733999999999952 #### 3443
0.07732000000000028 #### 3444
0.07729999999999926 #### 3445
0.07728000000000002 #### 3446
0.07723999999999975 #### 3447
0.07719999999999949 #### 3448
0.07718000000000025 #### 3449
0.07715999999999923 #### 3450
0.07715999999999923 #### 3451
0.07713999999999999 #### 3452
0.07713999999999999 #### 3453
0.07711999999999897 #### 3454
0.0770799999999987 #### 3455
0.07704000000000022 #### 3456
0.07704000000000022 #### 3457
0.0770199999999992 #### 3458
0.07699999999999996 #### 3459
0.07697999999999894 #### 3460
0.07699999999999996 #### 3461
0.07704000000000022 #### 3462
0.07705999999999946 #### 3463
0.0770999999

0.07638000000000034 #### 5163
0.0762799999999988 #### 5164
0.07615999999999978 #### 5165
0.07607999999999926 #### 5166
0.07599999999999874 #### 5167
0.07593999999999923 #### 5168
0.0758599999999987 #### 5169
0.07577999999999996 #### 5170
0.07572000000000045 #### 5171
0.07568000000000019 #### 5172
0.07561999999999891 #### 5173
0.07554000000000016 #### 5174
0.0754400000000004 #### 5175
0.07533999999999885 #### 5176
0.07523999999999909 #### 5177
0.07513999999999932 #### 5178
0.07503999999999955 #### 5179
0.07491999999999877 #### 5180
0.07484000000000002 #### 5181
0.07471999999999923 #### 5182
0.07463999999999871 #### 5183
0.0745799999999992 #### 5184
0.0745199999999997 #### 5185
0.07447999999999944 #### 5186
0.07441999999999993 #### 5187
0.07437999999999967 #### 5188
0.07436000000000043 #### 5189
0.07432000000000016 #### 5190
0.0742799999999999 #### 5191
0.07425999999999888 #### 5192
0.07423999999999964 #### 5193
0.0742200000000004 #### 5194
0.07423999999999964 #### 5195
0.074279999999999

0.04654000000000025 #### 7105
0.04651999999999923 #### 7106
0.04647999999999897 #### 7107
0.046439999999998705 #### 7108
0.04640000000000022 #### 7109
0.04633999999999894 #### 7110
0.04627999999999943 #### 7111
0.04619999999999891 #### 7112
0.04616000000000042 #### 7113
0.04616000000000042 #### 7114
0.04619999999999891 #### 7115
0.04619999999999891 #### 7116
0.046179999999999666 #### 7117
0.04619999999999891 #### 7118
0.04621999999999993 #### 7119
0.04627999999999943 #### 7120
0.04630000000000045 #### 7121
0.046319999999999695 #### 7122
0.046319999999999695 #### 7123
0.046319999999999695 #### 7124
0.04633999999999894 #### 7125
0.046319999999999695 #### 7126
0.04630000000000045 #### 7127
0.04623999999999917 #### 7128
0.04619999999999891 #### 7129
0.046179999999999666 #### 7130
0.046179999999999666 #### 7131
0.04616000000000042 #### 7132
0.046139999999999404 #### 7133
0.04609999999999914 #### 7134
0.04605999999999888 #### 7135
0.046020000000000394 #### 7136
0.046020000000000394 #### 7137

...

0.026659999999999684 #### 92460
0.02657999999999916 #### 92461
0.026519999999999655 #### 92462
0.02643999999999913 #### 92463
0.026360000000000383 #### 92464
0.02632000000000012 #### 92465
0.02625999999999884 #### 92466
0.026220000000000354 #### 92467
0.026159999999999073 #### 92468
0.02611999999999881 #### 92469
0.026059999999999306 #### 92470
0.025979999999998782 #### 92471
0.025900000000000034 #### 92472
0.025839999999998753 #### 92473
0.025779999999999248 #### 92474
0.025719999999999743 #### 92475
0.025660000000000238 #### 92476
0.025579999999999714 #### 92477
0.02552000000000021 #### 92478
0.025479999999999947 #### 92479
0.025439999999999685 #### 92480
0.025420000000000442 #### 92481
0.025399999999999423 #### 92482
0.025399999999999423 #### 92483
0.025420000000000442 #### 92484
0.025459999999998928 #### 92485
0.025479999999999947 #### 92486
0.025479999999999947 #### 92487
0.02549999999999919 #### 92488
0.02552000000000021 #### 92489
0.025539999999999452 #### 92490
0.02555999999999

0.01966000000000001 #### 93899
0.019679999999999254 #### 93900
0.019719999999999516 #### 93901
0.01973999999999876 #### 93902
0.019759999999999778 #### 93903
0.019759999999999778 #### 93904
0.019759999999999778 #### 93905
0.019759999999999778 #### 93906
0.019759999999999778 #### 93907
0.01977999999999902 #### 93908
0.019819999999999283 #### 93909
0.019840000000000302 #### 93910
0.019859999999999545 #### 93911
0.019879999999998788 #### 93912
0.01991999999999905 #### 93913
0.01994000000000007 #### 93914
0.01995999999999931 #### 93915
0.019999999999999574 #### 93916
0.020019999999998817 #### 93917
0.019999999999999574 #### 93918
0.019999999999999574 #### 93919
0.019999999999999574 #### 93920
0.019999999999999574 #### 93921
0.019999999999999574 #### 93922
0.019999999999999574 #### 93923
0.01998000000000033 #### 93924
0.01994000000000007 #### 93925
0.01994000000000007 #### 93926
0.01994000000000007 #### 93927
0.019899999999999807 #### 93928
0.019879999999998788 #### 93929
0.0198599999999995

0.014239999999999142 #### 95542
0.01419999999999888 #### 95543
0.01419999999999888 #### 95544
0.014179999999999637 #### 95545
0.014179999999999637 #### 95546
0.014160000000000394 #### 95547
0.014120000000000132 #### 95548
0.014099999999999113 #### 95549
0.014059999999998851 #### 95550
0.013999999999999346 #### 95551
0.013980000000000103 #### 95552
0.013939999999999841 #### 95553
0.013919999999998822 #### 95554
0.013919999999998822 #### 95555
0.013959999999999084 #### 95556
0.013980000000000103 #### 95557
0.013959999999999084 #### 95558
0.013919999999998822 #### 95559
0.013919999999998822 #### 95560
0.013919999999998822 #### 95561
0.013919999999998822 #### 95562
0.013959999999999084 #### 95563
0.013999999999999346 #### 95564
0.014039999999999608 #### 95565
0.014059999999998851 #### 95566
0.01407999999999987 #### 95567
0.014099999999999113 #### 95568
0.014120000000000132 #### 95569
0.014139999999999375 #### 95570
0.01419999999999888 #### 95571
0.0142199999999999 #### 95572
0.014260000000

0.0056200000000004025 #### 97191
0.00558000000000014 #### 97192
0.005539999999999878 #### 97193
0.005519999999998859 #### 97194
0.0054800000000003735 #### 97195
0.005399999999999849 #### 97196
0.005359999999999587 #### 97197
0.005300000000000082 #### 97198
0.005239999999998801 #### 97199
0.005179999999999296 #### 97200
0.005160000000000053 #### 97201
0.005139999999999034 #### 97202
0.005139999999999034 #### 97203
0.005160000000000053 #### 97204
0.005160000000000053 #### 97205
0.005160000000000053 #### 97206
0.005139999999999034 #### 97207
0.005139999999999034 #### 97208
0.005139999999999034 #### 97209
0.005119999999999791 #### 97210
0.005099999999998772 #### 97211
0.005099999999998772 #### 97212
0.005079999999999529 #### 97213
0.0050600000000002865 #### 97214
0.005079999999999529 #### 97215
0.0050600000000002865 #### 97216
0.005039999999999267 #### 97217
0.005039999999999267 #### 97218
0.0050600000000002865 #### 97219
0.0050600000000002865 #### 97220
0.005039999999999267 #### 97221
0.0

0.0029000000000003467 #### 98766
0.0029000000000003467 #### 98767
0.0029000000000003467 #### 98768
0.0029199999999995896 #### 98769
0.0029000000000003467 #### 98770
0.0028600000000000847 #### 98771
0.0027999999999988034 #### 98772
0.0027799999999995606 #### 98773
0.0027200000000000557 #### 98774
0.0026399999999995316 #### 98775
0.0025800000000000267 #### 98776
0.0025399999999997647 #### 98777
0.0024800000000002598 #### 98778
0.0023799999999987165 #### 98779
0.0022999999999999687 #### 98780
0.0022199999999994446 #### 98781
0.0021399999999989205 #### 98782
0.0020799999999994156 #### 98783
0.0020199999999999108 #### 98784
0.0019200000000001438 #### 98785
0.0017999999999993577 #### 98786
0.0016999999999995907 #### 98787
0.0015799999999988046 #### 98788
0.0014799999999990376 #### 98789
0.00140000000000029 #### 98790
0.0013199999999997658 #### 98791
0.0012399999999992417 #### 98792
0.0011599999999987176 #### 98793
0.0010799999999999699 #### 98794
0.0009999999999994458 #### 98795
0.0008999999

In [15]:
(num_flippable_prime[(i+1):] * num_flippable_prime[:-(i+1)]).mean()

9.191599151862688

In [ ]:
for i in range(100):
    print((num_flippable_prime[::i+2][1:] * num_flippable_prime[::i+2][:-1]).mean())

In [ ]:
samples_state.shape

In [ ]:
P1 = ma.der_log(samples_state)

In [ ]:
P2 = ma.der_log_new(samples_state)

In [ ]:
P1

In [ ]:
P2

In [ ]:
index.shape

In [ ]:
ma._ws.size

In [ ]:
for i in range(index.shape[0]):
    index[i][np.argwhere(ma._der_mat_symm[:,i]).reshape(-1)] = True 

In [ ]:
index.shape

In [ ]:
index.shape

In [ ]:
out = np.empty((index.shape[0],ma._outb.shape[0],index.shape[1]), dtype=np.float)

In [ ]:
T_samples_state = samples_state[:,ma._autom]

In [ ]:
tanh = np.tanh(T_samples_state.dot(ma._ws))

In [ ]:
ma._outb[0][:10]

In [ ]:
A = np.einsum('ijk,ijl->ikl',T_samples_state, tanh)

In [ ]:
np.round(A.reshape(A.shape[0],-1),7) == np.round(P,7)

In [ ]:
P

In [ ]:
A.reshape(A.shape[0],-1)

In [ ]:
A[0]

In [ ]:
np.round(ma._outb,8) == round(A[0,0,0,0],8)

In [ ]:
samples_state.dot(ma._w)[0] == T_samples_state.dot(ma._ws)[0,0,0]

In [ ]:
ma._autom.shape

In [ ]:
T_samples_state.dot(ma._ws).shape

In [ ]:
T_samples_state.dot(ma._ws)[0,0,1]

In [ ]:
T_samples_state.dot(ma._ws)

In [ ]:
(ma._w.T == ma._ws[ma._autom][0][:,0]).all(axis=1)

In [ ]:
(P == np.einsum('ijk,ijl->ikl',samples_state_, tan)[0,0,0]).any()

In [ ]:
r_ = r.reshape(r.shape[0], ma._ws.shape[1],-1).transpose((0,2,1))

In [ ]:
r_.reshape(-1,r_.shape[2])

In [ ]:
%time np.einsum('ijk,ikl->ikjl',r_,samples_state[:,ma._autom])

In [ ]:
temp = samples_state[:,ma._autom]

In [ ]:
%timeit np.einsum("ij,il->ijl", temp.reshape(-1,temp.shape[-1]), r_.reshape(-1,r_.shape[2]))

In [ ]:
ma._w.size

In [ ]:
ma._outb.reshape((ma._outb.shape[0],) + ma._w.shape).shape

In [ ]:
out.sum(axis=2)[0] == out1.sum(axis=2)[:,0].real

In [ ]:
out.sum(axis=2)

In [ ]:
out1.sum(axis=2).real

In [ ]:
out1 = ma._outb[:, index]

In [ ]:
ma._der_mat_symm.shape

In [ ]:
np.argwhere(ma._der_mat_symm[:,0])

In [ ]:
ma._der_mat_symm.shape

In [ ]:
ma._autom.shape

In [ ]:
ma._outb.shape

In [ ]:
import mkl
import time
mkl.set_num_threads(12)
%timeit ma._outb @ ma._der_mat_symm

In [ ]:
h = 1
q = 1.1
length = [4, 4]
V = h * q
ham = f.dimer_hamiltonian(V, h , length)

g = nk.graph.Graph(nodes = [i for i in range(length[0] * length[1] * 2)])
hi = nk.hilbert.Spin(s=0.5, graph=g)
op_transition2 = f.dimer_flip2(length = np.array(length))
op_transition1 = f.dimer_flip1(length = np.array(length))

alpha = 1
hex_ = nk.machine.new_hex(np.array(length))
ma = nk.machine.RbmDimer(hi,hex_, alpha = alpha, symmetry = True, reverse=True
                    ,use_hidden_bias = False, use_visible_bias = False, dtype=float)
ma.init_random_parameters(seed=1234)

In [ ]:
kernel = 1
n_chains = 1
n_iter = 600
sweep_size = 100
decay_factor = 1 # or 'sigmoid decay'
n_jobs = 6

sa = nk.sampler.DimerMetropolisLocal(machine=ma, op=op_transition1, length = length, sweep_size = sweep_size, n_chains = n_chains, kernel = kernel)
sa_mul = nk.sampler.DimerMetropolisLocal_multi(machine=ma, op=op_transition1, length = length, n_chains=n_chains, sweep_size = sweep_size, kernel = 1, n_jobs=n_jobs)

sr = nk.optimizer.SR(ma, diag_shift=0)
opt = nk.optimizer.Sgd(ma, learning_rate=0.05, decay_factor = decay_factor ,N = n_iter)
gs = nk.Vmc(
hamiltonian=ham,
sampler=sa_mul,
optimizer=opt,
n_samples=6000,
sr = sr,
n_discard = 300,
)



In [ ]:
gs.run(n_iter=n_iter)

In [ ]:
sa = nk.sampler.DimerMetropolisLocal(machine=ma, op=op_transition1, length = length, sweep_size = sweep_size, n_chains = n_chains, kernel = kernel)
sa.sample_shape